As part of the Pizza and remote sensing of the WISE 2024 workshop in Cargese.

This Jupyter notebook will use the SEAScope viewer and SEAScope Python bindings to retrieve inputs data

* author: dr.fab, OceanDataLab
* date: 2024-04-23


# Study wave propagation from the cross spectra between Sentinel2 optical channels

Sentinel-2 data are great to estimate wave properties in cloud free conditions and in the presence of sun or sky glitter.

The different optical bands of Sentinel2 are sensing the sea surface at slightly different times since the different detectors for each band are placed at a slighly different place in the MSI camera focal plane, creating an optical parallax.

This notebook will teach you how to:
* Import data from SEAScope
* Investigate cross spectra between optical Sentinel2 optical channels

<div class="alert alert-warning">
<strong>This notebook uses the following data collection:</strong>

* directory: `sentinel-2_rgb`

Check that you have them in your SEAScope catalogue before continuing with this notebook<br>
These collections can be downloaded at https://ftp.odl.bzh/odl/events/wise2024/IDF_SEAScope/sentinel-2_rgb

To learn how to add data to SEAScope, you can watch one of the following YouTube videos:
* [How to add data to SEAScope on **Windows**](https://youtu.be/TsJSg7V7WNU?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=2)
    * or the "Add data to SEAScope" chapter of [How to add data to SEAScope on **Windows**](https://youtu.be/uomHRQPgqb8?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=3&t=40s)
* [How to add data to SEAScope on **macOS**](https://youtu.be/s5X3ewpmcuw?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=5)
* [How to add data to SEAScope on **Linux**](https://youtu.be/3ZAzgl3v2lo?list=PL_Nrq3gZvmM_C8baJBiNEzMjg0Hg7FIgK&index=8)
</div>

In [ ]:
import os
import numpy
from numpy.fft import fft2, fftshift, ifft2, fftfreq
import math
import matplotlib
%matplotlib inline
import matplotlib.pyplot as plt
import matplotlib.cm as cm
from scipy import signal
import scipy.io as sp
from scipy.ndimage.filters import gaussian_filter
from scipy.interpolate import interp1d
from scipy.ndimage import rotate 
from numpy.lib.recfunctions import stack_arrays
from datetime import datetime,timedelta

## Extract Sentinel2 data from SEAScope



##### locate the Sentinel2 data in the SEAScope viewer

1. In the "Catalogue" (the panel on the right), select :
    * collection `Sentinel2 RGB`, variable `rgb`
    
2. Select the date where you have data available (highlighted in white in the timeline)
    * The 17<sup>th</sup> of February 2024 should be good
3. Locate the data on the globe
    * It should be in the Agulhas current region

##### Steps for data extraction from SEAScope

1. Zoom-in to properly see the waves  (the resolution of the extraction depends on the zoom level)
2. Draw a polygon over the region you want to extract:
    1. Start drawing by clicking on the 3<sup>rd</sup> button to the right of the pen icon in the toolbar or by hitting the <kbd>P</kbd> key
    2. Place the corners of the polygon by left-clicking on the globe
    3. Once all the corners placed, hit the <kbd>Enter</kbd> or <kbd>Return</kbd> key to commit your polygon
3. Select the polygon you just created by clicking on it
4. Extract the data intersecting that polygon by clicking on the extract button in the "Selected annotation" panel

In [ ]:
# Load data directly from viewer memory
from SEAScope.lib import get_extracted_data
extractions = get_extracted_data()

In [ ]:
for k, data in enumerate(extractions.keys()):
    print('{} - {}'.format(k, os.path.basename(data)))
    print('\n'.join(['\t{}'.format(x) for x in extractions[data]['data']]))

## Play with the data
** Compute Cross spectra and compare the phase to the linear dispertion relation: <br> **

In [ ]:
granule_uri =  next( v for i, v in enumerate(extractions.keys()) if i == 0)
extraction = extractions[granule_uri]
start = extraction['meta']['start']
print(extraction['meta']['fields'])

<span style="color:red"> ** Selection of the two channels you want to compare: <br>**
B02_TOA_reflectance is the blue channel <br>
B04_TOA_reflectance is the red channel <br>
</span>

In [ ]:
### Set name_var_b4 and name_var_b6
name_var_b4 = 'B04_TOA_reflectance'
name_var_b2 = 'B02_TOA_reflectance'
# Extract data
extraction = extractions[granule_uri]   
b4 = extraction['data'][name_var_b4]
b2 = extraction['data'][name_var_b2]

** Plot first channel **

In [ ]:
fig = plt.figure(figsize=(16,10))
plt.imshow(numpy.flipud(b2),interpolation='bicubic',cmap='gray')
cbar=plt.colorbar()

## Crop the image borders to avoid missing data in FFT calculations
* Define cropped pixels amount (by default 50) to remove borders with missing data 

In [ ]:
# define the numbers of pixels to crop from the border (will be applied to crop left, right, up, down)
crop = 50
b4_crop = b4[crop:-crop, crop:-crop]
b2_crop = b2[crop:-crop, crop:-crop]
fig = plt.figure(figsize=(16,10))
plt.imshow(numpy.flipud(b2_crop),interpolation='bicubic',cmap='gray')
cbar=plt.colorbar()

In [ ]:
# Reconstruct coordinates and compute ground_spacing
from SEAScope.lib.utils import get_lonlat
lon2D, lat2D = get_lonlat(extraction, numpy.shape(b4))
ground_spacing = (lat2D[int(b4.shape[0]/2+1), int(b4.shape[1]/2)]
                  - lat2D[int(b4.shape[0]/2),int(b4.shape[1]/2)]) * 100000
print(ground_spacing)

In [ ]:
def rebin(a, shape):
    sh = shape[0],a.shape[0]//shape[0],shape[1],a.shape[1]//shape[1]
    return a.reshape(sh).mean(-1).mean(1)

In [ ]:
def looks2xspec(im1,im2,periodo_size):
    imshape = numpy.array(im1.shape, dtype='int32')

    ###########################################################################
    # Set periodograms/looks/specs sizes and positions
    ###########################################################################

    aziwindow = numpy.hanning(periodo_size+2)[1:-1]
    ranwindow = numpy.hanning(periodo_size+2)[1:-1]
    window = numpy.sqrt(numpy.outer(aziwindow, ranwindow))
    ###########################################################################
    # Compute periodograms and compute co/cross spectra
    ###########################################################################

    count = numpy.ceil(imshape[0]/periodo_size).astype('int32')
    perpos = (numpy.floor(numpy.linspace(0, imshape[0]-periodo_size, num=count)+0.5).astype('int32'),
              numpy.floor(numpy.linspace(0, imshape[1]-periodo_size, num=count)+0.5).astype('int32'))
    specshape = numpy.array((periodo_size, periodo_size), dtype='int32')
    specs = numpy.zeros(specshape, dtype='complex64')

    for appos in iter(perpos[0]):
        for rppos in iter(perpos[1]):
            sub1 = im1[appos:appos+periodo_size, rppos:rppos+periodo_size]
            sub1 = sub1 - numpy.mean(sub1)
            per1 = fftshift(fft2(sub1*window))/periodo_size
            sub2 = im2[appos:appos+periodo_size, rppos:rppos+periodo_size]
            sub2 = sub2 - numpy.mean(sub2)
            per2 = fftshift(fft2(sub2*window))/periodo_size
            specs += per1 * numpy.conj(per2)
            
    specs[int(periodo_size/2-2):int(periodo_size/2+3), int(periodo_size/2-2):int(periodo_size/2+3)] = 0
    specs[int(periodo_size/2-3):int(periodo_size/2+4), int(periodo_size/2)] = 0
    specs[int(periodo_size/2), int(periodo_size/2-3):int(periodo_size/2+4)] = 0

    return specs

In [ ]:
# Define period to compute spectrum
periodo_size = 128
spec = looks2xspec(b4_crop, b2_crop,periodo_size)

In [ ]:
kran = (numpy.arange(periodo_size)-periodo_size/2.)/periodo_size*2*numpy.pi/ground_spacing
kazi = (numpy.arange(periodo_size)-periodo_size/2.)/periodo_size*2*numpy.pi/ground_spacing
fig = plt.figure(figsize = (14,14))
plt.subplot(2, 2, 1)
plt.imshow(numpy.log(numpy.flipud(numpy.abs(spec))), extent=[kran[0], kran[-1],
            kazi[-1], kazi[1]], aspect='auto',cmap='jet')
plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('Absolute value')
plt.colorbar()
plt.subplot(2, 2, 2)
plt.imshow(numpy.flipud(numpy.real(spec)*1e5), extent=[kran[0], kran[-1],
            kazi[-1], kazi[1]],aspect='auto',cmap='jet')
plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('Real Part')
plt.colorbar()
plt.subplot(2, 2, 3)
plt.imshow(numpy.flipud(numpy.imag(spec)*1e5), extent=[kran[0], kran[-1],
            kazi[-1], kazi[1]],aspect='auto',cmap='jet')
plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('Imaginary part')
plt.colorbar()
plt.subplot(2, 2, 4)
plt.imshow(numpy.flipud(numpy.angle(spec)*180/numpy.pi), extent=[kran[0], kran[-1],
           kazi[-1], kazi[1]],aspect='auto',cmap='jet',vmin=-60,vmax=60)
plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('Phase (deg)')
plt.colorbar()

In [ ]:
kran = (numpy.arange(periodo_size)-periodo_size/2.)/periodo_size*2*numpy.pi/ground_spacing
kazi = (numpy.arange(periodo_size)-periodo_size/2.)/periodo_size*2*numpy.pi/ground_spacing
fig = plt.figure(figsize = (16,14))
pi = numpy.pi
cut = int(periodo_size/4)

from scipy.signal import medfilt
# plt.imshow(numpy.flipud(numpy.abs(spec[cut:-cut+1,cut:-cut-1])*1e-5), extent=[kran[0+cut], kran[-1-cut],
#             kazi[-1-cut], kazi[1+cut]], aspect='auto',cmap='jet')
plt.imshow(medfilt(numpy.log(numpy.flipud(numpy.abs(spec[cut:-cut+1,cut:-cut-1]*1e5))),3), extent=[kran[0+cut], kran[-1-cut],
            kazi[-1-cut], kazi[1+cut]], aspect='auto',cmap='jet')

kcircle=[2*pi/800, 2*pi/400, 2*pi/200, 2*pi/100]
theta = 2. * pi * numpy.linspace(0, 1, num=361)
for kcir in kcircle:
    plt.plot(kcir*numpy.cos(theta), kcir*numpy.sin(theta), ':b')
    kcirstr = '%im' % (numpy.round(2*numpy.pi/kcir))
    plt.text(0, -(kcir+.003), kcirstr, ha='center', va='top',fontsize=None,color='black')

plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('Absolute value')
plt.colorbar()

## Rotate the spectrum to have the maximum energy in the horizontal direction
* Adapt the rotation angle until the spectum maximum energy is aligned with horizontal direction

In [ ]:
rotation_angle =45#! parameter that may be changed to align energy with horizontal axis

rot_spec_imag = rotate(numpy.imag(spec),rotation_angle,reshape=False)
rot_spec_real = rotate(numpy.real(spec),rotation_angle,reshape=False)
rot_spec = rot_spec_real + complex(0,1)*rot_spec_imag

fig = plt.figure(figsize = (16,14))
cut = int(periodo_size/4)
plt.imshow(numpy.log(numpy.flipud(numpy.abs(rot_spec[cut:-cut+1,cut:-cut-1]))), extent=[kran[0+cut], kran[-1-cut],
            kazi[-1-cut], kazi[1+cut]], aspect='auto',cmap='jet')
kcircle=[2*pi/800, 2*pi/400, 2*pi/200, 2*pi/100]
theta = 2. * pi * numpy.linspace(0, 1, num=361)
for kcir in kcircle:
    plt.plot(kcir*numpy.cos(theta), kcir*numpy.sin(theta), ':b')
    kcirstr = '%im' % (numpy.round(2*numpy.pi/kcir))
    plt.text(0, -(kcir+.003), kcirstr, ha='center', va='top',fontsize=None,color='black')

plt.xlabel('wavenumber [rad/m]')
plt.ylabel('wavenumber [rad/m]')
plt.title('Absolute value')
plt.colorbar()


## estimate phase velocity
* <span style="color:red"> Define time shift between the two bands (variable shift_time_bands). </span> <br>
If you are comparing red and blue channels shift_time_bands is around 0.95. More information can be found in the Sentinel 2 documentation.

In [ ]:
fig = plt.figure(figsize = (10,10))
shift_time_bands = 0.95

mini = int(periodo_size/2+4)
spec = looks2xspec(b4_crop, b2_crop,periodo_size)
vphase = numpy.angle(numpy.mean(rot_spec[int(periodo_size/2-4):int(periodo_size/2+4),mini:-5],axis=0)) / kran[mini:-5] / shift_time_bands
sp = numpy.mean(numpy.real(rot_spec[:,mini:-5]),axis=0)/numpy.mean(numpy.real(spec[:,mini:-5]))
plt.plot(kran[mini:-5],vphase, 'b', label='observed phase velocity')
plt.plot(kran[mini:-5],sp*2, 'g', label='observed spectrum')
plt.plot(kran[mini:-5],numpy.sqrt(9.81/kran[mini:-5]), 'r', label='theoretical phase velocity')
plt.plot(kran[mini:-5],-numpy.sqrt(9.81/kran[mini:-5]), 'r')

plt.ylim(-30,30)
plt.xlim(0.01,0.08)
plt.legend()
plt.xlabel('wavenumber')
plt.ylabel('phase velocity m/s')
